In [8]:
#The Gaussian eliminator for systems of linear equations in the matrix form (TMA4115, Spring 2022/23)
#Feel free to experiment with the code. If you find any bugs, please send a message to artur.rutkowski@ntnu.no
from sympy import *
import numpy as np
def dataverify(A):#Verify if the entered data is fine
    if isinstance(A,Matrix) == 0:#Check if the entered data is a matrix
        return "Error. Wrong data type."
    else:
        if A.cols < 2 or A.rows < 1:#Check if there is at least one variable and one equation
            return "Error. Wrong matrix size."
    vnum=A.cols-1#The number of variables
    enum=A.rows#The number of equations
    for i in range(vnum):
        if A[:,i] == zeros(1,enum):#Check if there are columns containing only zeros. This aspect of the program could be improved by handling the zero columns in the actual algorithm, and print an additional (free) variables corresponding to them
            return "Error. Remove zero columns." 
    return 1
def Gauss(A):
    if dataverify(A) != 1:
        return dataverify(A)
    vnum=A.cols-1#The number of variables
    enum=A.rows#The initial number of equations
    diagsize=min(enum,vnum)#The maximal number of pivot elements that we can expect
    print(np.matrix(A))
    input()
    
    ##################Procedure for the row echelon form
    print("Start row echelon form.")
    input()
    pivotlocs = []
    cpl = (0,0) #current pivot location
    i=0
    while i<diagsize:                   #Number of the column in which we want to produce the pivot element
        ispivot = 1
        if(A[cpl]==0):                          #If there is zero on the current pivot position
            ispivot = 0
            for l in range(cpl[0]+1,enum):      #search if there is an appropriate row to switch it with
                if(A[l,cpl[1]] !=0):            #If a non-zero element is found below the current pivot position, switch rows
                    B = A[l,:]
                    A[l,:] = A[cpl[0],:]
                    A[cpl[0],:] = B
                    ispivot = 1                 
                    pivotlocs.append(cpl)       #Add the current location to the list of locations of pivot elements
                    print(np.matrix(A))
                    input()
                    break
        else:
            ispivot = 1
            pivotlocs.append(cpl)
        if(ispivot == 0):                            #If there is no pivot element in this column 
            cpl = tuple(map(sum, zip(cpl, (0,1))))   #try obtaining a pivot element in the next column and the same row
            if cpl[1]==vnum:                         #Once the current pivot location gets to the last column, terminate the procedure
                break   
        else:                                   #If there is a pivot element in this column: 
            for j in range(cpl[0]+1,enum):      #1)Produce zeroes below the current pivot element
                multiplier = A[j,i]/A[cpl]
                if (multiplier != 0):
                    for k in range (i,vnum+1):      #Make changes in row j
                        A[j,k] = A[j,k] - multiplier*A[cpl[0],k]
                    print(np.matrix(A))
                    input()
            cpl = tuple(map(sum, zip(cpl, (1,1)))) #2) on the next round of the i-loop try getting a pivot element in the next column and the next row
            i+=1
    print("Row echelon form:\n", np.matrix(A))  
    pivotcols = [i[1] for i in pivotlocs]             #List of columns in which there is a pivot element
                
    ###################Remove 0=0 equations and check if there are 0=b(!=0) equations.
    for i in range(enum-1,len(pivotlocs)-1,-1):
            if(A[i,vnum]!=0):              #If the right hand side is non-zero, then we get 0=b
                 return "The system has no solutions."
            else:                          #Otherwise we get 0=0, so we can remove the equation
                A.row_del(i)    
    input()
    print("Redundant rows removed:\n", np.matrix(A))  
    
    ################Normalize pivot elements
    for i in range(len(pivotcols)):       
        if(A[pivotlocs[i]]!=0 and A[pivotlocs[i]]!=1):
            mult = A[pivotlocs[i]]
            for j in range(pivotcols[i],vnum+1):
                A[i,j] = A[i,j]/mult
    input()
    print("Normalized pivot elements:\n", np.matrix(A))
    
    ##################Loop producing reduced row echelon form
    #NB: in the following we go from left to right, starting from the second pivot element
    #This is slightly different from what we did in the interactive lecture, but also leads to the solution
    print("Start reduced row echelon form.")
    input()
    for i in range(len(pivotcols)):                   #Number of the column which we want to clear
        for j in range(pivotlocs[i][0]):              #j=number of the row above the current pivot element that we are currently looking at
            multiplier = A[j,pivotcols[i]]/A[pivotlocs[i]]
            if (multiplier !=0):
                for k in range (i,vnum+1):      #Make changes in row j
                    A[j,k] = A[j,k] - multiplier*A[i,k]
                print(np.matrix(A))
                input()
    print("Reduced row echelon form:\n", np.matrix(A))
    
    ###################Print solutions
    input()
    if (A.cols == A.rows+1):       #If at this point we are left with the same number of variables and equations, then we get a unique solution
        print("The unique solution is:")
        for i in range(vnum):
            print ("x"+str(i+1),"=",A[i,vnum])
    else:                          #Otherwise we get infinitely many solutions
        par = A.cols - 1 - A.rows
        print("There are infinitely many solutions. The family of solutions has ", par, "real parameter(s).")
        X = np.matrix(["x"+str(i+1) for i in range(vnum)]).transpose()   #We will print the solution in a vector form
        parcols = list(set(range(vnum)).difference(pivotcols))  #Variables corresponding to columns without a pivot element are taken as parameters
        print("The solution is:")
        print(X,"=")
        B =[]
        j=0
        for i in range(vnum):
            if (i in parcols):
                B.append(0)
            else:
                B.append(A[j,vnum])
                j+=1
        print(np.matrix(B).transpose())        
        for i in range(len(parcols)):#Print vector corresponding to i-th parameter
            B=[]
            k=0
            for j in range(vnum):
                if (j in parcols):
                    B.append(int(j==parcols[i]))
                else:
                    B.append(-A[k,parcols[i]])
                    k+=1
            print("+t"+str(i+1)+"*", np.matrix(B).transpose(),"\n")
        
       
            
      
        
#A = Matrix(([12,4,1,10],[3,2,1,3],[3,-2,1,7]))
#A = Matrix(([1,2,3],[-1,-1,-1],[2,4,6]))
#A = Matrix(([12,4,1,2,10],[3,2,1,2,3]))
A = Matrix(([4,2,12,1,0,10],[2,2,3,1,0,3],[-1,1,0,1,0,0],[0,0,0,0,1,2]))
#A = Matrix(([12,4,1,10],[3,2,1,3],[3,-2,1,7],[1,2,3,4],[2,3,0,0]))
Gauss(A)


[[4 2 12 1 0 10]
 [2 2 3 1 0 3]
 [-1 1 0 1 0 0]
 [0 0 0 0 1 2]]


Start row echelon form.


[[4 2 12 1 0 10]
 [0 1 -3 1/2 0 -2]
 [-1 1 0 1 0 0]
 [0 0 0 0 1 2]]


[[4 2 12 1 0 10]
 [0 1 -3 1/2 0 -2]
 [0 3/2 3 5/4 0 5/2]
 [0 0 0 0 1 2]]


[[4 2 12 1 0 10]
 [0 1 -3 1/2 0 -2]
 [0 0 15/2 1/2 0 11/2]
 [0 0 0 0 1 2]]


...

[[1 0 9/2 0 0 7/2]
 [0 1 -3 1/2 0 -2]
 [0 0 1 1/15 0 11/15]
 [0 0 0 0 1 2]]


[[1 0 0 -3/10 0 1/5]
 [0 1 -3 1/2 0 -2]
 [0 0 1 1/15 0 11/15]
 [0 0 0 0 1 2]]


[[1 0 0 -3/10 0 1/5]
 [0 1 0 7/10 0 1/5]
 [0 0 1 1/15 0 11/15]
 [0 0 0 0 1 2]]


Reduced row echelon form:
 [[1 0 0 -3/10 0 1/5]
 [0 1 0 7/10 0 1/5]
 [0 0 1 1/15 0 11/15]
 [0 0 0 0 1 2]]


There are infinitely many solutions. The family of solutions has  1 real parameter(s).
The solution is:
[['x1']
 ['x2']
 ['x3']
 ['x4']
 ['x5']] =
[[1/5]
 [1/5]
 [11/15]
 [0]
 [2]]
+t1* [[3/10]
 [-7/10]
 [-1/15]
 [1]
 [0]] 

